## Import / Config

In [ ]:
import pandas as pd
from sqlalchemy import create_engine, text
import cred_pg as c
import folium

In [ ]:
engine = create_engine(
    f'postgresql://{c.pg_userid}:{c.pg_password}@{c.pg_host}/{c.pg_db}', 
    connect_args = {'options': '-c search_path=$user,ugeobln,umisc,umobility,usozmed,public', 'keepalives_idle': 120},
    pool_size=1, 
    max_overflow=0,
    execution_options={ 'isolation_level': 'AUTOCOMMIT' }
)

In [ ]:
# engine.dispose()

## Data

In [ ]:
lat_lng_ml_krhs = (52.4907, 13.2914)
lat_lng_schmargendorf = (52.4787, 13.2919)

## Functions

In [ ]:
def cmarker(color, radius):
  return folium.CircleMarker(radius=radius, weight=0, fill_color=color, fill_opacity=1)

def tmarker(text):
    return folium.Marker(icon=folium.DivIcon(html=text))

def add_to_map(m, df, tooltip_fn, marker_fn, style_fn):
    for x in df.apply(lambda r: folium.GeoJson(
            r.gj, 
            tooltip=tooltip_fn(r),
            marker=marker_fn(r),
            style_function=style_fn
            ), axis=1):
        x.add_to(m)

def get_osm(kind, lat, lng, bb_size_in_degree):
    sql = f"""
    select osm_id as osmid, fclass, name as descr, ST_AsGeoJSON(geometry) as gj
    from 
      gis_osm_{kind}_free_1 osm, 
      (select ST_Expand(ST_Point({lng}, {lat}, 4326), {bb_size_in_degree}) bb) x 
    where 
      ST_Intersects(osm.geometry, x.bb); 
    """
    with engine.connect() as con:
        df = pd.read_sql_query(text(sql), con)
    return df


## Geofabrik

In [ ]:
m = folium.Map(location=lat_lng_ml_krhs, zoom_start=15)
# df = get_osm("pois_a", *lat_lng_ml_krhs, 0.005)
df = get_osm("buildings_a", *lat_lng_ml_krhs, 0.005)

tooltip = lambda r: f'{r["osmid"]}|{r["fclass"]}|{r["descr"]}'
marker = lambda r: cmarker("red", 4)
style = lambda feature: {"color": "green", "fillColor": "green", "fillOpacity": 0.5}
add_to_map(m, df, tooltip, marker, style)
m